In [ ]:
# better formatting for large floats
import pandas as pd
pd.options.display.float_format = "{:,.2f}".format

In [ ]:
from risk.swaptions import get_swaption_portfolio
import datetime
from utils.db import dbconn
from analytics import init_ontr
conn = dbconn('dawndb')
conn.autocommit = True
init_ontr()

In [ ]:
portf = get_swaption_portfolio(datetime.date.today(), conn, source_list=['GS'])
portf

In [ ]:
df = portf._todf()
positions = df.set_index("Index")[["Delta", "Notional"]].prod(axis=1).groupby(level="Index").sum()
positions.name = 'current_delta'
gamma = df.set_index("Index")[["Gamma", "Notional"]].prod(axis=1).groupby(level="Index").sum()
gamma.name = 'gamma'

In [ ]:
hedges = pd.read_sql_query("SELECT security_desc, notional FROM list_cds_positions_by_strat(%s) "
                           "WHERE folder in ('IGOPTDEL', 'HYOPTDEL')",
                           conn, params=(datetime.date.today(),))

In [ ]:
def f(s):
    l = s.split(" ")
    return f"{l[1]}{l[3][1:]} {l[4].lower()}r"

hedges["Index"] = hedges["security_desc"].apply(f)
hedges = hedges.rename(columns={"notional": "current hedge"})
hedges = hedges.set_index("Index")["current hedge"]
hedges = hedges.reindex(positions.index, fill_value=0.)
risk = pd.concat([hedges, positions, gamma], axis=1)
risk['net_delta'] = risk["current hedge"] + risk.current_delta
risk

In [ ]:
from analytics.scenarios import run_portfolio_scenarios
from analytics import BlackSwaptionVolSurface, CreditIndex
import analytics
import datetime
import numpy as np

today = datetime.datetime.now()
yesterday = datetime.date.today() - pd.offsets.BDay()

portf = get_swaption_portfolio(yesterday, conn, source_list=['GS'])
for i, amt in hedges.iteritems():
    portf.add_trade(CreditIndex(i[:2], i[2:4], '5yr', value_date=yesterday, notional=amt), ('delta', i))

vol_surface = {}
for trade in portf.swaptions:
    vs = BlackSwaptionVolSurface(trade.index.index_type, trade.index.series, 
                                 value_date=today.date(), interp_method = "bivariate_linear")
    vol_surface[(trade.index.index_type, trade.index.series, trade.option_type)] = vs[vs.list(source='GS', option_type=trade.option_type)[-1]]

#Set original_pv as of yesterday's EOD levels, don't reset PV after this time
portf.mark(interp_method="bivariate_linear", source_list=['GS'])
portf.reset_pv()

#set ref to today's levels
portf.value_date = today
portf.mark(interp_method="bivariate_linear", source_list=['GS'])

spread_shock = np.round(np.arange(-.1, .1, .01), 4)
scens = run_portfolio_scenarios(portf, [today], params=['pnl', 'hy_equiv', 'sigma'],
                                spread_shock=spread_shock,
                                vol_shock=[0],
                                corr_shock=[0],
                                vol_surface=vol_surface)
pnl = scens.xs('pnl', level = 2, axis=1).sum(axis=1)
hy_equiv = scens.xs('hy_equiv', level = 2, axis=1).sum(axis=1)

ig = CreditIndex('IG', 32, '5yr', value_date = today)
ig.mark()

pnl.index = pnl.index.set_levels((1+pnl.index.get_level_values('spread_shock')) * ig.spread, level = 'spread_shock')
hy_equiv.index = pnl.index

In [ ]:
pnl, hy_equiv